
# Set Jenkins Jobs

This jobs is used to add jobs to a :epkg:`Jenkins` server in order
to build packages on Windows. The :epkg:`YAML` definition is located
at [pymyinstall/whl](https://github.com/sdpython/pymyinstall/tree/master/whl)
and it defines the jobs in this folder
[pymyinstall/whl/windows](https://github.com/sdpython/pymyinstall/tree/master/whl/windows).


imports



In [ ]:
import sys
import os
import warnings

from pyquickhelper.jenkinshelper import setup_jenkins_server_yml, JenkinsExt
from pyquickhelper.loghelper import fLOG, get_user

Starts logging.



In [ ]:
fLOG(OutputPrint=True)
fLOG("start")

password



In [ ]:
with warnings.catch_warnings():
    warnings.simplefilter('ignore', DeprecationWarning)
    import keyring
user = keyring.get_password("jenkins", "user")
pwd = keyring.get_password("jenkins", "pwd")

local path



In [ ]:
key = "Python%d%d" % sys.version_info[:2]
engines = {key: os.path.abspath(os.path.dirname(sys.executable))}
if sys.platform.startswith("win"):
    folder = f"C:\\{get_user()}\\github\\_whl"
    location = "c:\\jenkins\\pymy"
    suf = "win"
else:
    folder = f"/home/{get_user()}/github/_whl"
    location = "/usr/local/Python%d.%d" % sys.version_info[:2]
    suf = "lin"

In [ ]:
if not os.path.exists("build"):
    os.mkdir("build")

Loads the yml template.



In [ ]:
yml = os.path.join(folder, f".local.jenkins.{suf}.yml")
with open(yml, "r", encoding="utf-8") as f:
    content = f.read()

Starts the Jenkins server.



In [ ]:
js = JenkinsExt('http://localhost:8080/', user,
                pwd, fLOG=fLOG, engines=engines)

Defines the Jenkins job.



In [ ]:
ymls = []
for mod in ["polylearn", "dynd-python"]:
    new_content = content.replace("__MODULE__", mod)
    yml = os.path.join(
        "build", f".local.jenkins.lin.{mod}.yml")
    with open(yml, "w", encoding="utf-8") as f:
        f.write(new_content)
    batch = os.path.join(folder, "windows", f"build_{mod}.bat")
    with open(batch, "r", encoding="utf-8") as f:
        cbat = f.read()
    with open(yml, "w", encoding="utf-8") as f:
        f.write(new_content)
    toadd = [dict(name=f"build_{mod}.bat",
                  content=cbat)]
    ymls.append(("yml", yml, dict(scripts=toadd)))

Update the Jenkins jobs for the given set of modules



In [ ]:
fLOG("Update jenkins")
setup_jenkins_server_yml(js, github=None, modules=ymls,
                         overwrite=True, location=location, prefix="",
                         delete_first=False, disable_schedule=False, fLOG=fLOG)
fLOG("Done")